In [95]:
# !pip install opencv-python
# !pip install pandas

In [1]:
import cv2
import numpy as np
from keras.models import model_from_json

In [2]:
emotion_dictionary = {0: "Angry", 1: "Disgusted", 2: "Fearful", 3: "Happy", 4: "Neutral", 5: "Sad", 6: "Surprised"}

# Load the model
json_file = open("model/emotion_model.json", "r")
loaded_model_json = json_file.read()
json_file.close()
emotion_model = model_from_json(loaded_model_json)

In [3]:
emotion_model.load_weights("model/emotion_model.h5")
print("Loaded model from disk")

Loaded model from disk


In [4]:
video_capture = cv2.VideoCapture("E:\\Level 04\\Academic 2023\\Research Group\\implementation\\data\\video\\sandali.mp4")
video_capture = cv2.VideoCapture(0)

while False:

    if (video_capture.isOpened()== False): 
        print("Error opening video stream or file")
        break

    try:
        # haar cascade for face detection
        ret, frame = video_capture.read()
        frame = cv2.resize(frame, (640, 360))
        if not ret:
            break
        bounding_box = cv2.CascadeClassifier('haarcascade/haarcascade_frontalface_default.xml')
        gray_frame = cv2.cvtColor(frame, cv2.COLOR_BGR2GRAY)

        num_faces = bounding_box.detectMultiScale(gray_frame, scaleFactor=1.3, minNeighbors=5)

        # Draw rectangles around each face
        for (x, y, w, h) in num_faces:
            cv2.rectangle(frame, (x, y-50), (x+w, y+h+10), (255, 0, 0), 2) # blue rectangle for face
            roi_gray_frame = gray_frame[y:y + h, x:x + w] # crop the face
            cropped_img = np.expand_dims(np.expand_dims(cv2.resize(roi_gray_frame, (48, 48)), -1), 0) # resize the face to 48x48

            # predict the emotion
            emotion_prediction = emotion_model.predict(cropped_img) # predict the emotion
            maxindex = int(np.argmax(emotion_prediction)) # get the index of max emotion
            cv2.putText(frame, emotion_dictionary[maxindex], (x+20, y-60), cv2.FONT_HERSHEY_SIMPLEX, 1, (255, 255, 255), 2, cv2.LINE_AA) # put the emotion text on the frame
        
        cv2.imshow('Emotion Detection', cv2.resize(frame,(640,360),interpolation = cv2.INTER_CUBIC))
        cv2.imshow('Emotion Detection', frame)
        if cv2.waitKey(1) & 0xFF == ord('q'):
            break
    except Exception as e:
        print(e)

video_capture.release()
cv2.destroyAllWindows()

In [27]:
def identify_emotion_of_video(file_name_with_extension):

    emotion_array = [0, 0, 0, 0, 0, 0, 0]

    file_path = "E:\\Level 04\\Academic 2023\\Research Group\\implementation\\data\\video\\" + file_name_with_extension

    print(file_path)

    try:
        video_capture = cv2.VideoCapture(file_path) # 0

        # get the number of frames
        no_of_frames = int(video_capture.get(cv2.CAP_PROP_FRAME_COUNT))

        FRAME_SKIP_COUNT = 5

        i=0
        while i < no_of_frames:
            if (video_capture.isOpened()== False): 
                print("Error opening video stream or file")
                break

            try:
                # haar cascade for face detection
                ret, frame = video_capture.read()
                frame = cv2.resize(frame, (640, 360))
                if not ret:
                    break
                bounding_box = cv2.CascadeClassifier('haarcascade/haarcascade_frontalface_default.xml')
                gray_frame = cv2.cvtColor(frame, cv2.COLOR_BGR2GRAY)

                num_faces = bounding_box.detectMultiScale(gray_frame, scaleFactor=1.3, minNeighbors=5)

                for (x, y, w, h) in num_faces:
                    cv2.rectangle(frame, (x, y-50), (x+w, y+h+10), (255, 0, 0), 2) # blue rectangle for face
                    roi_gray_frame = gray_frame[y:y + h, x:x + w] # crop the face
                    cropped_img = np.expand_dims(np.expand_dims(cv2.resize(roi_gray_frame, (48, 48)), -1), 0) # resize the face to 48x48

                    # predict the emotion
                    emotion_prediction = emotion_model.predict(cropped_img) # predict the emotion
                    maxindex = int(np.argmax(emotion_prediction)) # get the index of max emotion
                    # cv2.putText(frame, emotion_dictionary[maxindex], (x+20, y-60), cv2.FONT_HERSHEY_SIMPLEX, 1, (255, 255, 255), 2, cv2.LINE_AA) # put the emotion text on the frame

                    emotion_array[maxindex] += 1
                
                # cv2.imshow('Emotion Detection', cv2.resize(frame,(640,360),interpolation = cv2.INTER_CUBIC))
                # cv2.imshow('Emotion Detection', frame)
                # if cv2.waitKey(1) & 0xFF == ord('q'):
                #     break
            except Exception as e:
                print(e)
            i += FRAME_SKIP_COUNT

        video_capture.release()
        cv2.destroyAllWindows()

    except Exception as e:
        print("No file found in the given path : " + file_path)

    return emotion_array

In [25]:
import math

def get_emotion_percentage(student_id):
    file_name_with_extension = student_id + ".mp4"
    emotion_list = identify_emotion_of_video(file_name_with_extension)
    emotion_percentage_list = []
    total = sum(emotion_list)
    if total == 0:
        return [0,0,0,0,0,0,0]
    for i in emotion_list:
        emotion_percentage_list.append(round((i/total)*100, 2))
    return emotion_percentage_list

In [18]:
import pandas as pd
import numpy as np

In [19]:
data_set = 'E:\\Level 04\\Academic 2023\\Research Group\\implementation\\data\\student_engagment_dataset.csv'

df = pd.read_csv(data_set)
df.head()

Id            Timestamp                 Name  \
0   2  22/12/2022 16:46:16         DulmiNiwanka   
1   3  22/12/2022 17:41:30        PrasadiHerath   
2   4  22/12/2022 18:28:47     BhagyaGunarathna   
3   5  22/12/2022 23:16:19  DinushaThrilakshika   
4   6  22/12/2022 23:38:22      ShanikaSewwandi   

  Give some percentage(%) about your engagement level?\nExample : 80%  
0                                                20%                   
1                                                10%                   
2                                                20%                   
3                                                90%                   
4                                                30%

In [20]:
# Rename the column
df.rename(columns={'Id': 'id', 'Timestamp':'time','Name': 'name','Give some percentage(%) about your engagement level?\nExample : 80%': 'engagement_level'}, inplace=True)
df.head()

id                 time                 name engagement_level
0   2  22/12/2022 16:46:16         DulmiNiwanka              20%
1   3  22/12/2022 17:41:30        PrasadiHerath              10%
2   4  22/12/2022 18:28:47     BhagyaGunarathna              20%
3   5  22/12/2022 23:16:19  DinushaThrilakshika              90%
4   6  22/12/2022 23:38:22      ShanikaSewwandi              30%

In [21]:
df.dtypes

id                   int64
time                object
name                object
engagement_level    object
dtype: object

In [22]:
# remove percentage sign of engagement_level feature and convert to float
df['engagement_level'] = df['engagement_level'].str.replace('%', '').astype(float)
df.head()

id                 time                 name  engagement_level
0   2  22/12/2022 16:46:16         DulmiNiwanka              20.0
1   3  22/12/2022 17:41:30        PrasadiHerath              10.0
2   4  22/12/2022 18:28:47     BhagyaGunarathna              20.0
3   5  22/12/2022 23:16:19  DinushaThrilakshika              90.0
4   6  22/12/2022 23:38:22      ShanikaSewwandi              30.0

In [23]:
# add new columns to the dataframe
df['angry'] = 0
df['disgusted'] = 0
df['fearful'] = 0
df['happy'] = 0
df['neutral'] = 0
df['sad'] = 0
df['surprised'] = 0

df.head()

id                 time                 name  engagement_level  angry  \
0   2  22/12/2022 16:46:16         DulmiNiwanka              20.0      0   
1   3  22/12/2022 17:41:30        PrasadiHerath              10.0      0   
2   4  22/12/2022 18:28:47     BhagyaGunarathna              20.0      0   
3   5  22/12/2022 23:16:19  DinushaThrilakshika              90.0      0   
4   6  22/12/2022 23:38:22      ShanikaSewwandi              30.0      0   

   disgusted  fearful  happy  neutral  sad  surprised  
0          0        0      0        0    0          0  
1          0        0      0        0    0          0  
2          0        0      0        0    0          0  
3          0        0      0        0    0          0  
4          0        0      0        0    0          0

In [28]:
# assign values of emotion percentage to the dataframe
total_emotions_of_dataset = []
for index, row in df.iterrows():
    student_id = df.at[index, 'id']
    emotion_percentage_list = get_emotion_percentage(str(student_id))
    df.at[index, 'angry'] = emotion_percentage_list[0]
    df.at[index, 'disgusted'] = emotion_percentage_list[1]
    df.at[index, 'fearful'] = emotion_percentage_list[2]
    df.at[index, 'happy'] = emotion_percentage_list[3]
    df.at[index, 'neutral'] = emotion_percentage_list[4]
    df.at[index, 'sad'] = emotion_percentage_list[5]
    df.at[index, 'surprised'] = emotion_percentage_list[6]
    total_emotions_of_dataset.append(emotion_percentage_list)
    
    # write the dataframe to a csv file
    df.to_csv('E:\\Level 04\\Academic 2023\\Research Group\\implementation\\data\\student_engagement_dataset_labeled_with_emotion_percentage.csv', index=False)

# df.head()

E:\Level 04\Academic 2023\Research Group\implementation\data\video\2.mp4
1/1 [==============================] - 0s 26ms/step
E:\Level 04\Academic 2023\Research Group\implementation\data\video\3.mp4
1/1 [==============================] - 0s 28ms/step
E:\Level 04\Academic 2023\Research Group\implementation\data\video\4.mp4
1/1 [==============================] - 0s 29ms/step
E:\Level 04\Academic 2023\Research Group\implementation\data\video\5.mp4
1/1 [==============================] - 0s 39ms/step
E:\Level 04\Academic 2023\Research Group\implementation\data\video\6.mp4
1/1 [==============================] - 0s 43ms/step
E:\Level 04\Academic 2023\Research Group\implementation\data\video\7.mp4
1/1 [==============================] - 0s 52ms/step
E:\Level 04\Academic 2023\Research Group\implementation\data\video\8.mp4
1/1 [==============================] - 0s 49ms/step
E:\Level 04\Academic 2023\Research Group\implementation\data\video\9.mp4
1/1 [==============================] - 0s 49ms/step


KeyboardInterrupt: 

In [8]:
df.head()

time               name  engagement_level  Angry  Disgusted  \
0  25/12/2022 15:42:13    BandaraK.D.H.S.                 5   10.8          0   
1  14/03/2023 15:08:48    SasikaSankalana                75   10.8          0   
2  14/03/2023 17:19:44  SandaliWijerathna                 5   10.8          0   

   Fearful  Happy  Neutral  Sad  Surprised  
0      5.2     25     10.8    0       48.2  
1      5.2     25     10.8    0       48.2  
2      5.2     25     10.8    0       48.2